## Comparison of execution of VerticalPvConfiguration and DefaultConfiguration using the posterior parameters from net_photosynthetic_rate_hyperborla - trial 3 - Using different crop_growth_regulating_factor for intercropping

In [3]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [4]:
import numpy as np
import pandas as pd

from agrivoltaics_supply_side_management.agriculture.crops import Cultivation
from agrivoltaics_supply_side_management.configuration \
    import VerticalPvConfiguration, DefaultConfiguration
from agrivoltaics_supply_side_management.optimization.convex_optimization\
    import ConvexOptimization
from agrivoltaics_supply_side_management.photovoltaics.pv_modules\
    import ElectricityGeneration
from agrivoltaics_supply_side_management.solar_irradiation.irradiance\
    import IrradianceManager

In [5]:
monocropping_phi, monocropping_alpha, monocropping_theta, monocropping_p_max = \
    0.03442841710379512, 0.09510809834054065, 1.327579142408395, 25.0

In [6]:
monocropping_net_photosynthetic_rate_parameters = {
                "phi": monocropping_phi,
                "alpha": monocropping_alpha,
                "theta": monocropping_theta,
                "p_max": monocropping_p_max
            }

In [7]:
intercropping_phi, intercropping_alpha, intercropping_theta, intercropping_p_max = \
    0.05498625745316387, 0.12013631354448669, 0.7442598071555129, 17.0

In [8]:
intercropping_net_photosynthetic_rate_parameters = {
                "phi": intercropping_phi,
                "alpha": intercropping_alpha,
                "theta": intercropping_theta,
                "p_max": intercropping_p_max
            }

In [9]:
posterior_intercropping_phi, posterior_intercropping_alpha, posterior_intercropping_theta, posterior_intercropping_p_max = \
    0.26, 0.22, -1.4, 17.0

In [10]:
posterior_intercropping_net_photosynthetic_rate_parameters = {
                "phi": posterior_intercropping_phi,
                "alpha": posterior_intercropping_alpha,
                "theta": posterior_intercropping_theta,
                "p_max": posterior_intercropping_p_max
            }

In [11]:
lattitude, longitude = 49.26757152616243, -123.25266177347093
timezone = 'Canada/Pacific'
time_range = pd.date_range('2022-07-06', '2022-07-07', freq='1T',
                             tz=timezone)

In [12]:
irradiance_manager = IrradianceManager(lattitude, longitude, timezone, time_range)

In [13]:
optimization = ConvexOptimization()

In [14]:
electricity_generation = ElectricityGeneration()

In [15]:
harvest_index = 0.95
biomass_energy_ratio = 30
leaf_area_index = 5

In [16]:
default_crop_growth_regulating_factor = 0.95

In [17]:
default_cultivation = Cultivation(harvest_index, biomass_energy_ratio,
                          leaf_area_index, default_crop_growth_regulating_factor)

##### Take into account the difference in net photosynthetic rate at light saturation point

In [18]:
monocropping_net_photosynthetic_rate_at_light_saturation_point = 12.5
intercropping_net_photosynthetic_rate_at_light_saturation_point = 11.0

intercropping_crop_growth_regulating_factor = default_crop_growth_regulating_factor * (
    intercropping_net_photosynthetic_rate_at_light_saturation_point / monocropping_net_photosynthetic_rate_at_light_saturation_point)

In [19]:
intercropping_crop_growth_regulating_factor

0.836

In [20]:
intercropping_cultivation = Cultivation(harvest_index, biomass_energy_ratio,
                          leaf_area_index, intercropping_crop_growth_regulating_factor)

In [21]:
ppfd_data = np.linspace(0, 1500)

### Default configuration

In [22]:
default_configuration = DefaultConfiguration(
    monocropping_net_photosynthetic_rate_parameters, ppfd_data,
    irradiance_manager, optimization, electricity_generation,
    default_cultivation)

In [23]:
default_electricity_supply, default_crop_yield, \
    default_cumulative_electric_power_for_morning_peak, \
    default_cumulative_electric_power_for_afternoon_peak \
        = default_configuration.supply(time_range)

GLPSOL--GLPK LP/MIP Solver 5.0
Parameter(s) specified in the command line:
 --write /var/folders/8n/f15shvd92vv8t4gykc82yrdm0000gn/T/tmpy42pc4_e.glpk.raw
 --wglp /var/folders/8n/f15shvd92vv8t4gykc82yrdm0000gn/T/tmp40wg1ip3.glpk.glp
 --cpxlp /var/folders/8n/f15shvd92vv8t4gykc82yrdm0000gn/T/tmpohhsc32x.pyomo.lp
Reading problem data from '/var/folders/8n/f15shvd92vv8t4gykc82yrdm0000gn/T/tmpohhsc32x.pyomo.lp'...
3 rows, 3 columns, 4 non-zeros
25 lines were read
Writing problem data to '/var/folders/8n/f15shvd92vv8t4gykc82yrdm0000gn/T/tmp40wg1ip3.glpk.glp'...
18 lines were written
GLPK Simplex Optimizer 5.0
3 rows, 3 columns, 4 non-zeros
Preprocessing...
~     0: obj =   0.000000000e+00  infeas =  0.000e+00
OPTIMAL SOLUTION FOUND BY LP PREPROCESSOR
Time used:   0.0 secs
Memory used: 0.0 Mb (32525 bytes)
Writing basic solution to '/var/folders/8n/f15shvd92vv8t4gykc82yrdm0000gn/T/tmpy42pc4_e.glpk.raw'...
15 lines were written
GLPSOL--GLPK LP/MIP Solver 5.0
Parameter(s) specified in the comman

In [24]:
default_electricity_supply

918.9715900202176

In [25]:
default_crop_yield

0.0027233276629629963

In [26]:
default_cumulative_electric_power_for_morning_peak

91.8278328954443

In [27]:
default_cumulative_electric_power_for_afternoon_peak

234.95319208297147

### Vertical configuration with prior values

In [28]:
vertical_configuration = VerticalPvConfiguration(
    intercropping_net_photosynthetic_rate_parameters, ppfd_data,
    irradiance_manager, optimization, electricity_generation,
    intercropping_cultivation)

In [29]:
vertical_electricity_supply, vertical_crop_yield,\
    vertical_cumulative_electric_power_for_morning_peak, \
    vertical_cumulative_electric_power_for_afternoon_peak \
        = vertical_configuration.supply(time_range)

GLPSOL--GLPK LP/MIP Solver 5.0
Parameter(s) specified in the command line:
 --write /var/folders/8n/f15shvd92vv8t4gykc82yrdm0000gn/T/tmpj4pax2_j.glpk.raw
 --wglp /var/folders/8n/f15shvd92vv8t4gykc82yrdm0000gn/T/tmpqw6nb93g.glpk.glp
 --cpxlp /var/folders/8n/f15shvd92vv8t4gykc82yrdm0000gn/T/tmp0lt6dxzr.pyomo.lp
Reading problem data from '/var/folders/8n/f15shvd92vv8t4gykc82yrdm0000gn/T/tmp0lt6dxzr.pyomo.lp'...
3 rows, 3 columns, 4 non-zeros
25 lines were read
Writing problem data to '/var/folders/8n/f15shvd92vv8t4gykc82yrdm0000gn/T/tmpqw6nb93g.glpk.glp'...
18 lines were written
GLPK Simplex Optimizer 5.0
3 rows, 3 columns, 4 non-zeros
Preprocessing...
~     0: obj =   0.000000000e+00  infeas =  0.000e+00
OPTIMAL SOLUTION FOUND BY LP PREPROCESSOR
Time used:   0.0 secs
Memory used: 0.0 Mb (32525 bytes)
Writing basic solution to '/var/folders/8n/f15shvd92vv8t4gykc82yrdm0000gn/T/tmpj4pax2_j.glpk.raw'...
15 lines were written
GLPSOL--GLPK LP/MIP Solver 5.0
Parameter(s) specified in the comman

In [30]:
vertical_electricity_supply

997.7126392686137

In [31]:
vertical_crop_yield

0.0026552644792800116

In [32]:
vertical_cumulative_electric_power_for_morning_peak

207.5421186097299

In [33]:
vertical_cumulative_electric_power_for_afternoon_peak

408.52462065440017

### Vertical configuration with posterior values

In [34]:
posterior_vertical_configuration = VerticalPvConfiguration(
    posterior_intercropping_net_photosynthetic_rate_parameters, ppfd_data,
    irradiance_manager, optimization, electricity_generation,
    intercropping_cultivation)

In [35]:
posterior_vertical_electricity_supply, posterior_vertical_crop_yield,\
    posterior_vertical_cumulative_electric_power_for_morning_peak, \
    posterior_vertical_cumulative_electric_power_for_afternoon_peak \
        = posterior_vertical_configuration.supply(time_range)

GLPSOL--GLPK LP/MIP Solver 5.0
Parameter(s) specified in the command line:
 --write /var/folders/8n/f15shvd92vv8t4gykc82yrdm0000gn/T/tmpokblalei.glpk.raw
 --wglp /var/folders/8n/f15shvd92vv8t4gykc82yrdm0000gn/T/tmpbxza9ooj.glpk.glp
 --cpxlp /var/folders/8n/f15shvd92vv8t4gykc82yrdm0000gn/T/tmpgq70st03.pyomo.lp
Reading problem data from '/var/folders/8n/f15shvd92vv8t4gykc82yrdm0000gn/T/tmpgq70st03.pyomo.lp'...
3 rows, 3 columns, 4 non-zeros
25 lines were read
Writing problem data to '/var/folders/8n/f15shvd92vv8t4gykc82yrdm0000gn/T/tmpbxza9ooj.glpk.glp'...
18 lines were written
GLPK Simplex Optimizer 5.0
3 rows, 3 columns, 4 non-zeros
Preprocessing...
~     0: obj =   0.000000000e+00  infeas =  0.000e+00
OPTIMAL SOLUTION FOUND BY LP PREPROCESSOR
Time used:   0.0 secs
Memory used: 0.0 Mb (32525 bytes)
Writing basic solution to '/var/folders/8n/f15shvd92vv8t4gykc82yrdm0000gn/T/tmpokblalei.glpk.raw'...
15 lines were written
GLPSOL--GLPK LP/MIP Solver 5.0
Parameter(s) specified in the comman

In [36]:
posterior_vertical_electricity_supply

1169.0877499400572

In [37]:
posterior_vertical_crop_yield

0.0019824311331770187

In [38]:
posterior_vertical_cumulative_electric_power_for_morning_peak

207.5421186097299

In [39]:
posterior_vertical_cumulative_electric_power_for_afternoon_peak

408.52462065440017

### Comparison

In [40]:
vertical_electricity_supply / default_electricity_supply

1.0856838776122162

In [41]:
vertical_crop_yield / default_crop_yield

0.9750073468541308

In [42]:
vertical_cumulative_electric_power_for_morning_peak / default_cumulative_electric_power_for_morning_peak

2.2601221445140554

In [43]:
vertical_cumulative_electric_power_for_afternoon_peak / default_cumulative_electric_power_for_afternoon_peak

1.7387489696676843

In [44]:
posterior_vertical_electricity_supply / default_electricity_supply

1.2721696324848704

In [45]:
posterior_vertical_crop_yield / default_crop_yield

0.7279444042440791

In [46]:
posterior_vertical_cumulative_electric_power_for_morning_peak / default_cumulative_electric_power_for_morning_peak

2.2601221445140554

In [47]:
posterior_vertical_cumulative_electric_power_for_afternoon_peak / default_cumulative_electric_power_for_afternoon_peak

1.7387489696676843

### Temp

In [50]:
posterior_intercropping_phi_old, posterior_intercropping_alpha_old, posterior_intercropping_theta_old, posterior_intercropping_p_max_old = \
    0.18, 0.14, -3.4, 17.0

In [51]:
posterior_intercropping_net_photosynthetic_rate_parameters_old = {
                "phi": posterior_intercropping_phi_old,
                "alpha": posterior_intercropping_alpha_old,
                "theta": posterior_intercropping_theta_old,
                "p_max": posterior_intercropping_p_max_old
            }

In [52]:
posterior_vertical_configuration_old = VerticalPvConfiguration(
    posterior_intercropping_net_photosynthetic_rate_parameters_old, ppfd_data,
    irradiance_manager, optimization, electricity_generation,
    intercropping_cultivation)

In [53]:
posterior_vertical_electricity_supply_old, posterior_vertical_crop_yield_old,\
    posterior_vertical_cumulative_electric_power_for_morning_peak_old, \
    posterior_vertical_cumulative_electric_power_for_afternoon_peak_old \
        = posterior_vertical_configuration_old.supply(time_range)

GLPSOL--GLPK LP/MIP Solver 5.0
Parameter(s) specified in the command line:
 --write /var/folders/8n/f15shvd92vv8t4gykc82yrdm0000gn/T/tmpu2thjg5u.glpk.raw
 --wglp /var/folders/8n/f15shvd92vv8t4gykc82yrdm0000gn/T/tmpqrfwd0zc.glpk.glp
 --cpxlp /var/folders/8n/f15shvd92vv8t4gykc82yrdm0000gn/T/tmpb8p_epqh.pyomo.lp
Reading problem data from '/var/folders/8n/f15shvd92vv8t4gykc82yrdm0000gn/T/tmpb8p_epqh.pyomo.lp'...
3 rows, 3 columns, 4 non-zeros
25 lines were read
Writing problem data to '/var/folders/8n/f15shvd92vv8t4gykc82yrdm0000gn/T/tmpqrfwd0zc.glpk.glp'...
18 lines were written
GLPK Simplex Optimizer 5.0
3 rows, 3 columns, 4 non-zeros
Preprocessing...
~     0: obj =   0.000000000e+00  infeas =  0.000e+00
OPTIMAL SOLUTION FOUND BY LP PREPROCESSOR
Time used:   0.0 secs
Memory used: 0.0 Mb (32525 bytes)
Writing basic solution to '/var/folders/8n/f15shvd92vv8t4gykc82yrdm0000gn/T/tmpu2thjg5u.glpk.raw'...
15 lines were written
GLPSOL--GLPK LP/MIP Solver 5.0
Parameter(s) specified in the comman

In [54]:
posterior_vertical_electricity_supply_old

1096.937728075854

In [55]:
posterior_vertical_crop_yield_old

0.0022656982916465147

In [56]:
posterior_vertical_cumulative_electric_power_for_morning_peak_old

207.5421186097299

In [57]:
posterior_vertical_cumulative_electric_power_for_afternoon_peak_old

408.52462065440017